In [31]:
import pandas as pd
from fitz import Rect


from pdf_scraper.doc_utils import open_exam
from pdf_scraper.block_utils import clean_blocks
from pdf_scraper.line_utils import print_line_table, get_line_df

1. Get all images.
2. Get all text lines.
3. Identify and Remove captions from text lines.
4. Identify and resort dual column text.

In [ ]:
def get_images(doc):
    images = []
    for i, page in enumerate(doc):
        page_blocks  = page.get_text("dict",sort=True)["blocks"]

        image_blocks = [block for block in page_blocks if     block["type"]]
        for image_block in image_blocks:
            image_block["page"]= i+1

        images.extend(image_blocks)

    return images

def get_doc_line_df(doc):
    dfs = []
    for i, page in enumerate(doc):
        page_blocks  = page.get_text("dict",sort=True)["blocks"]

        text_blocks  = [block for block in page_blocks if not block["type"]]
        text_blocks = clean_blocks(text_blocks)

        page_lines   = [ line for block in text_blocks for line in block["lines"]]
        page_df = get_line_df(page_lines)
        page_df["page"] = i+1
        page_df.sort_values("y0",inplace=True)
        dfs.append(page_df)
    grand_df = pd.concat(dfs,ignore_index=True)
    grand_df["dual_col"]=0

    return grand_df

In [ ]:
def get_captions(doc_df:pd.Dataframe, images:list[dict]):
   """
   This will return those rows of doc_df for which the rectangle formed by the
   columns: x0, y0, x1, y1 overlaps with any of the rectangles associated with
   the bboxes contained in the list of dict. The bboxes are tuples (x0,y0,x1,y1)
   """
   for image in images:
       x0,y0,x1,y1 = image["bbox"]

In [ ]:
from fitz import Rect
def get_captions(doc_df: pd.DataFrame, images: list[dict]) -> list[dict]:
    """
    For each image in `images`, add a 'caption' field containing the text from
    `doc_df` rows whose bounding boxes intersect with the image's bounding box.
    """
    for image in images:
        img_rect = Rect(*image["bbox"])
        captions = []

        for _, row in doc_df.iterrows():
            text_rect = Rect(row["x0"], row["y0"], row["x1"], row["y1"])
            if img_rect.intersects(text_rect):
                captions.append(str(row["text"]))

        image["caption"] = " ".join(captions).strip()

    return images

In [40]:
def get_captions(doc_df: pd.DataFrame, images: list[dict]) -> list[dict]:
    """
    Vectorized-ish approach to add captions to images based on overlapping boxes.
    """
    for image in images:
        img_rect = Rect(*image["bbox"])

        # Filter all potentially overlapping rows using bounding box logic
        overlap_mask = (
            (doc_df["x1"] > img_rect.x0) &
            (doc_df["x0"] < img_rect.x1) &
            (doc_df["y1"] > img_rect.y0) &
            (doc_df["y0"] < img_rect.y1) &
            (doc_df["page"] == image["page"] )
        )
        overlapping_rows = doc_df[overlap_mask]

        if len(overlapping_rows) > 0 and image["page"]!=1 :
            print(overlapping_rows[["text","page"]].head(4))

        # Optionally sort by vertical position (y0) if order matters
        overlapping_rows = overlapping_rows.sort_values(by="y0")

        # Collect and join the text
        image["caption"] = " ".join(overlapping_rows["text"].astype(str)).strip()

    return images

In [ ]:
import fitz  # PyMuPDF
from collections import defaultdict

# Load the uploaded PDF file
pdf_path = "/mnt/data/LC002ALP100EV_2006.pdf"
doc = fitz.open(pdf_path)

# We'll extract "real" images: only those larger than a reasonable size threshold
MIN_WIDTH = 50
MIN_HEIGHT = 50

# Dictionary to store filtered image info: page -> list of (xref, width, height, bbox)
filtered_images = defaultdict(list)

for page_num, page in enumerate(doc):
    images = page.get_images(full=True)
    for img in images:
        xref = img[0]
        pix = fitz.Pixmap(doc, xref)

        # If the image is a mask or a CMYK image (with alpha), convert to RGB
        if pix.n > 4:
            pix = fitz.Pixmap(fitz.csRGB, pix)

        if pix.width >= MIN_WIDTH and pix.height >= MIN_HEIGHT:
            # Try to find the bounding box from text dictionary, fallback to N/A
            bbox = None
            for block in page.get_text("dict")["blocks"]:
                if block["type"] == 1 and block.get("image") == xref:
                    bbox = block.get("bbox")
                    break

            filtered_images[page_num + 1].append({
                "xref": xref,
                "width": pix.width,
                "height": pix.height,
                "bbox": bbox if bbox else "N/A"
            })

doc.close()

filtered_images_summary = {k: len(v) for k, v in filtered_images.items()}
filtered_images_summary_sorted = dict(sorted(filtered_images_summary.items()))
filtered_images_summary_sorted

In [ ]:
# 2006 - no captions - many detected. Bad. Seems there are a million images linescanned across whole pdf.
# 2007 - no captions
# 2008 - no captions
# 2009 - no captions
# 2010 - no captions
# 2011 - Captions below images page 2 and 3.
# 2012 - Mostly good, then some captions below image.
# 2013 - page 3 and 2, image cut into slices, captions overlap with many. page 4 caption below image.
# 2014 - caption below image page 3. all others good
# 2015 - 2018 good
# 2019 - caption not contained in photo.
# 2020 - none (good)
# 2022 - good
# 2023 - good
# 2024 - good
# For caption prediction, we should have distance to nearest image
# distance to nearest text.
year=2006
doc = open_exam(year,"english","al",1)
doc_df = get_doc_line_df(doc)
images = get_images(doc)
print(len(images))
images = get_captions(doc_df, images)

       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I      2
       text  page
26  TEXT I

In [64]:
images[0]

{'number': 13170,
 'type': 1,
 'bbox': (67.02000427246094, 36.1796875, 117.30000305175781, 108.1796875),
 'width': 167,
 'height': 237,
 'ext': 'png',
 'colorspace': 1,
 'xres': 96,
 'yres': 96,
 'bpc': 8,
 'transform': (50.279998779296875,
  0.0,
  -0.0,
  72.0,
  67.02000427246094,
  36.1796875),
 'size': 3206,
 'image': b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\xa7\x00\x00\x00\xed\x08\x02\x00\x00\x00U\xb7\xf2\xb1\x00\x00\x00\tpHYs\x00\x00\x0e\xc4\x00\x00\x0e\xc4\x01\x95+\x0e\x1b\x00\x00\x0c8IDATx\x9c\xed\x9a\xdbr$)\x0cD\xf9\xff\x9f\xce\x8dX{\xdatq\xd3\x15\x04E>l\xb4)J)\xe9\x80z\xc6;\tW\xefSZ\x9d\x00[\xe9\x7f\xad\xcebom\xd6\xbe\x94iu.\x1bk\xb3\xde\xa5o\xadNgW\xed\xd4\xb8T\xd3\xea\xa4\xb6\xd4N]\xabR\xbf\xe0\x05\xda\xa6e-\xe4\x17\xbc@\xdb\xf4\xabO\xfd<\xf6\xaeE\xed\xd1)\n\xf2\xc3\xc0\xbb\x96\xb6A\x9b\xe8\xc8O\x02\xefZ\xe3\x06=\xe2R?\x00\xbcw\xa5\xd1\x1b$@~\x00\xfbK]\xa5\xd5\xe9\x0b\xf5j\xeaJ\xe4\xfb\xb2\xf7\xae+nG\xac\x90o\x07~BQq\xdbaK}#\xf6\x97\xfa\x1b\xc1O($t\x17\x9c\xc0\x07

In [84]:
from PIL import Image
from io import BytesIO

# Your image bytes (just an example snippet here)
img_bytes = images[7]["image"]

# Wrap the bytes in a BytesIO buffer
img_stream = BytesIO(img_bytes)

# Open the image using PIL
image = Image.open(img_stream)

# Show the image (optional)
#image.show()
display(image)

In [30]:
page_2_images = [image for image in images if image["page"]==3 and image["caption"] ]
print(len(page_2_images))

0


In [28]:
page_2_images[0]["caption"].isspace() or not page_2_images[0]["caption"]

True

In [5]:
grand_df.text.values[20:40]

array(['Question B. ',
       'N.B. Candidates may NOT answer a Question A and a Question B on the same text.  ',
       'SECTION II – COMPOSING ',
       '• Candidates must write on one of the compositions 1 – 7. ',
       'SECTION I                       COMPREHENDING                    (100 marks) ',
       'TEXT 1 – FROM GENRE to GENRE ',
       'This text consists of two elements: firstly, edited extracts adapted from Alan McMonagle’s essay, ',
       'The Misadventures of a Dithering Writer in Thirteen and A Half Fragments, in which he discusses ',
       'writing in different genres.  The second element is a genre-related cartoon by Tom Gauld. ',
       'I flit anxiously and eagerly from genre to genre.  ',
       'yourself be led by the child that you were.  This ',
       'I always have a few stories on the go.  Some of ',
       'is a tendency I adhered to upon my resumption ',
       'and, indeed, return to when it all threatens to ',
       'them are like eels – they slip a

In [ ]:
blocks=[]
images = []
dfs = []
for i, page in enumerate(doc):
    page_blocks  = page.get_text("dict",sort=True)["blocks"]

    text_blocks  = [block for block in page_blocks if not block["type"]]
    text_blocks = clean_blocks(text_blocks)

    image_blocks = [block for block in page_blocks if     block["type"]]
    for image_block in image_blocks:
        image_block["page"]= i+1

    page_lines   = [ line for block in text_blocks for line in block["lines"]]
    page_df = get_line_df(page_lines)
    page_df["page"] = i+1
    dfs.append(page_df)

grand_df = pd.concat(dfs,ignore_index=True)
grand_df["dual_col"]=0

# label dual column text

## Label page 2

In [16]:
grand_df[grand_df.page==2].text.head(15)

24    SECTION I                       COMPREHENDING ...
25                        TEXT 1 – FROM GENRE to GENRE 
26    This text consists of two elements: firstly, e...
27    The Misadventures of a Dithering Writer in Thi...
28    writing in different genres.  The second eleme...
29    I flit anxiously and eagerly from genre to gen...
30    yourself be led by the child that you were.  T...
31     I always have a few stories on the go.  Some of 
32       is a tendency I adhered to upon my resumption 
33     and, indeed, return to when it all threatens to 
34     them are like eels – they slip away if I do not 
35    make a fast grab.  Some are like bold children – 
36                                   get away from me. 
37      they pay absolutely no attention to anything I 
38     tell them to do.  One or two arrive unannounced 
Name: text, dtype: object

function
- takes in 4 lines: top left, top right, bottom left, bottom right
- makes copy of data frame
- identifies all lines between these. (max and min index)
- sorts this part of the data frame 
- returns tuple (sorted data frame, indices)

Then you can reassign this sorted data frame to the original data frame between
the provided indices.

Or else it can change the passed data frame in place which would be as useufl. 

In [17]:
def setDualCols(grand_df: pd.DataFrame, page_num:int, bookends: tuple[str]):
    page_df = grand_df[grand_df.page==page_num].copy()
    l1, r1, l2, r2 = bookends
    for line in bookends:
        print(page_df[page_df.text.str.contains(line)].index)
    indices = [page_df[page_df.text.str.contains(line)].index for line in bookends]
    top    = min(indices).values[0]
    bottom = max(indices).values[0]
    dual_cols = page_df[top:bottom+1].copy()
    dual_cols.sort_values(["x0","y0"],inplace=True)
    dual_cols["daul_col"]=1

    grand_df.loc[top:bottom+1] = dual_cols

    return grand_df


In [18]:
grand_df[grand_df.page==2].text.head(40)

24    SECTION I                       COMPREHENDING ...
25                        TEXT 1 – FROM GENRE to GENRE 
26    This text consists of two elements: firstly, e...
27    The Misadventures of a Dithering Writer in Thi...
28    writing in different genres.  The second eleme...
29    I flit anxiously and eagerly from genre to gen...
30    yourself be led by the child that you were.  T...
31     I always have a few stories on the go.  Some of 
32       is a tendency I adhered to upon my resumption 
33     and, indeed, return to when it all threatens to 
34     them are like eels – they slip away if I do not 
35    make a fast grab.  Some are like bold children – 
36                                   get away from me. 
37      they pay absolutely no attention to anything I 
38     tell them to do.  One or two arrive unannounced 
39      I am, at various times, a reluctant, plodding, 
40    instinctive, spontaneous writer.  At times I f...
41        from the farthest recesses of my imagi

In [19]:
line_l1 = "I flit anxious"
line_r1 = "yourself be led by the child"
line_lf = "imagination had not abandoned me"
line_rf = "lose almost all the time"

bookends = [line_l1,line_r1, line_lf, line_rf]

grand_df = setDualCols(grand_df, 2, bookends)

Index([29], dtype='int64')
Index([30], dtype='int64')
Index([106], dtype='int64')
Index([107], dtype='int64')


In [20]:
grand_df[grand_df.page==2].text.head(40)

24    SECTION I                       COMPREHENDING ...
25                        TEXT 1 – FROM GENRE to GENRE 
26    This text consists of two elements: firstly, e...
27    The Misadventures of a Dithering Writer in Thi...
28    writing in different genres.  The second eleme...
53                              immediate attention.   
54             I don’t know if my writing is in anyway 
55        I have started several novels.  There is the 
56    distinctive.  I am an aural learner as opposed...
57       edgy-existential one about the brother-sister 
58        assassination squad.  There is the comedy-of-
59            say the more common visual learning that 
60         attends so much writing.  I can hear things 
61      desperation one about the office slave finally 
62           tipped over the edge by a boss constantly 
63      before I see them.  My reasons for writing are 
64    partly intrinsic, partly spiritual, partly fan...
65       referred to as the highly evolved veget

In [75]:
page2_df = grand_df[grand_df.page==2].copy()
line_l1 = "I flit anxious"
line_r1 = "yourself be led by the child"

line_lf = "imagination had not abandoned me"
line_rf = "lose almost all the time"

bookends = [line_l1,line_r1, line_lf, line_rf]
for line in bookends:
    print(page2_df[page2_df.text.str.contains(line)].index)
indices = [page2_df[page2_df.text.str.contains(line)].index for line in bookends]
top = min(indices)
bottom = max(indices)

Index([29], dtype='int64')
Index([69], dtype='int64')
Index([68], dtype='int64')
Index([107], dtype='int64')


In [73]:
page2_text = page2_df[top.values[0]:bottom.values[0]+1].sort_values(["x0","y0"])
page2_text["dual_col"]=1

In [74]:
page2_text.text[36:50].values

array(['referred to as the highly evolved vegetable.  ',
       'There is the life-weary one about the last day ',
       'in the working life of a barber terrified beyond ',
       'measure of the imminent reunion with his ',
       'poet-activist daughter.  There is my novel ',
       'featuring an as-yet-to-be named antagonist ',
       'who is more of a genius in dreams than in life.  ',
       'I am all the time hankering to work on the very ',
       'project I am not currently tangled up inside.  ',
       'If you know what you want to be you will be it.  ',
       'If you don’t know, then you will spend your ',
       'days reinventing yourself, discovering who you ',
       'are.  I envy the former standpoint in so many ',
       'ways.  But I am an uncertain person and rather '], dtype=object)